<center><img src="../../../fig/ICHEC_Logo.jpg" alt="Drawing" style="width: 500px;"/><center/>

<center> <img src="../../../fig/notebooks/cythonlogo.png" alt="Drawing" style="width: 200px;"/>

***

# <center>Exercise 1: 10 minutes<center/>



* Define a simple addition module below, which containing the following function, and write it to a file `cython_addition.pyx`. Modify it to return `x + y`.

```python
def addition(x, y):
    # TODO
```

* Utilise the function by importing it into a new file `addition_main.py`
* Edit the `setup.py` accordingly to import the correct file. Use the demo as a reference

<div class="alert alert-block alert-info">
<b>Try the exercise outside the notebook environment using a text editor like vim or nano or another editor of your choosing <b/>   
</div>

In [9]:
%%writefile cython_addition.pyx

## TODO: Copy the above code into this cell and modify it to return x + y
def addition(x, y):
    print(x + y)

Writing cython_addition.pyx


In [10]:
%%writefile addition_main.py

## TODO: Import the function
from cython_addition import addition 
## TODO: Call the function
addition(2,3)

Writing addition_main.py


In [11]:
%%writefile setup.py

from distutils.core import setup, Extension
from Cython.Build import cythonize

# TODO: Edit the next line
setup(ext_modules = cythonize("cython_addition.pyx"))

Writing setup.py


In [12]:
!python setup.py build_ext --inplace

Compiling cython_addition.pyx because it changed.
[1/1] Cythonizing cython_addition.pyx
/ichec/home/staff/fisolomon/.conda/envs/python_hpc/lib/python3.7/site-packages/Cython/Compiler/Main.py:369: FutureWarning: Cython directive 'language_level' not set, using 2 for now (Py2). This will change in a later release! File: /ichec/home/staff/fisolomon/hpc-python/py-hpc-2022-05/03-Cython/exercise/cython_addition.pyx
  tree = Parsing.p_module(s, pxd, full_module_name)
running build_ext
building 'cython_addition' extension
gcc -pthread -B /ichec/home/staff/fisolomon/.conda/envs/python_hpc/compiler_compat -Wl,--sysroot=/ -Wsign-compare -DNDEBUG -g -fwrapv -O3 -Wall -Wstrict-prototypes -fPIC -I/ichec/home/staff/fisolomon/.conda/envs/python_hpc/include/python3.7m -c cython_addition.c -o build/temp.linux-x86_64-3.7/cython_addition.o
gcc -pthread -shared -B /ichec/home/staff/fisolomon/.conda/envs/python_hpc/compiler_compat -L/ichec/home/staff/fisolomon/.conda/envs/python_hpc/lib -Wl,-rpath=/ichec/ho

In [13]:
!python addition_main.py

5


***

# <center>Exercise 2: 5 minutes<center/>
    
* Consider the following python code which computes the integral for the function $x^2 - x$
* Run the code as is and record the time, $t_1$
* Use Cython's static type declarations on variables only and record the new time
* Repeat, and implement function call overheads. How has the time, $t_1$ changed? 
    * **Remember to use both `cdef` and `cpdef`**


In [15]:
%load_ext cython

In [16]:
%%cython -a 

def f(x):
    return x ** 2 - x

def integrate_f(a, b, N):
    s = 0
    dx = (b - a) / N
    for i in range(N):
        s += f(a + i * dx)
    return s * dx

In [17]:
%time integrate_f(9, 10, 100)

CPU times: user 177 µs, sys: 103 µs, total: 280 µs
Wall time: 290 µs


80.74334999999998

In [ ]:
%%cython

## TODO: redo previous code with static type declarations & function call overheads
def f(double x):
    return x ** 2 - x

def integrate_f(double a, double b, int N):
    cdef int s
    cdef double dx
    s = 0
    dx = (b - a) / N
    for i in range(N):
        s += f(a + i * dx)
    return s * dx

In [18]:
## TODO: record time of cython version, using %time (remember to use cpdef with %time)
%time integrate_f(9, 10, 100)

CPU times: user 48 µs, sys: 28 µs, total: 76 µs
Wall time: 103 µs


80.74334999999998

In [27]:
%%cython

## TODO: redo previous code with static type declarations & function call overheads
cdef int f_cdef(int x):
    return x ** 2 - x

cpdef double integrate_fcdef(double a, double b, int N):
    cdef int s
    cdef double dx
    s = 0
    dx = (b - a) / N
    for i in range(N):
        s += f_cdef(a + i * dx)
    return s * dx

In [28]:
## TODO: record time of cython version, using %time (remember to use cpdef with %time)
%time integrate_fcdef(9, 10, 100)

CPU times: user 0 ns, sys: 43 µs, total: 43 µs
Wall time: 63.7 µs


72.0

# <center>Additional Exercises<center/>

## Optimising with Cython 

- Based on a cProfile obtained for the simple (inefficient) heat equation script, write the `setup.py` file  that creates a Cython module for the most time consuming part of the script. Below is the beginning of the cProfile for [`heat_equation_simple.py`](./heat_equation_simple.py).

- In its current state, running the script can be done using the following command either in the terminal or using `!` from the notebook;

In [1]:
!python heat_equation_simple.py bottle.dat

Runtime: 20.442239999771118


- Using the inefficient script on the current setup the runtime of [`heat_equation_simple.py`](./heat_equation_simple.py) using;
    - [`bottle.dat`](./bottle.dat) ≃ ~20 secs
    - [`bottle_large.dat`](./bottle_large.dat) ≃ **~10 mins**
    

- The `time` module is being used to check the runtime of the `iterate` function, which implements `evolve`. The actual runtime of `heat_equation_simple.py` is slightly longer.

    
- How much can you improve the performance? You should be able to optimise it sufficiently to get the performance runtimes down to;
    - `bottle.dat` < 0.1 sec
    - `bottle_large.dat` < 5 secs
    
    
- Can you get it even better?
    
- **NB: Experiment with `bottle.dat` first, and ignore `bottle_large.dat` otherwise it will take too long! Get `bottle.dat` to run for ~0.5 secs before attempting with the larger dataset.**

<img src="cprofile.png" alt="Drawing" style="width: 600px;"/> 

- Use the code segment below from [`evolve.py`](./evolve.py) to create an `evolve.pyx` file. If you wish, you can copy this into a text editor of your choosing. 
    - Create a setup file to compile the code
    - Create the cython extension and investigate the effect on performance using any preferred timing technique.
    - Insert static type declarations, function calls, `cnp` arrays and compiler directives where necessary.

In [2]:
%%writefile evolve_cyt.pyx

import numpy as np
cimport numpy as cnp
import cython


@cython.boundscheck(False)
@cython.wraparound(False)
@cython.cdivision(True)

def evolve(cnp.ndarray[cnp.double_t , ndim =2]u , cnp.ndarray[cnp.double_t , ndim =2]u_previous, double a, double dt, double dx2, double dy2):
    
    cdef int n = u.shape[0]
    cdef int m = u.shape[1]

    cdef int i,j
    #multiplication is more efficient than division
    cdef double dx2inv = 1. / dx2
    cdef double dy2inv = 1. / dy2

    for i in range(1, n-1):
        for j in range(1, m-1):
            u[i, j] = u_previous[i, j] + a * dt * ( \
             (u_previous[i+1, j] - 2*u_previous[i, j] + \
              u_previous[i-1, j]) *dx2inv + \
             (u_previous[i, j+1] - 2*u_previous[i, j] + \
                 u_previous[i, j-1]) *dy2inv )
    u_previous[:] = u[:]

Writing evolve_cyt.pyx


In [3]:
%%writefile heat_setup.py

from distutils.core import setup, Extension
from Cython.Build import cythonize
import numpy


setup(ext_modules = cythonize("evolve_cyt.pyx"),include_dirs=[numpy.get_include()])

Writing heat_setup.py


In [4]:
!python heat_setup.py build_ext --inplace

Remember to import the correct module, `evolve` is different from `evolve_cyt`!

In [5]:
!python heat_equation_simple.py bottle.dat

Runtime: 18.84291100502014


### Bonus: 

- Compare with [`heat_equation_index.py`](./heat_equation_index.py) which uses array operations derived from [`evolve_index.py`](./evolve_index.py)
- What additional speed up can be found here?

In [6]:
!python heat_equation_index.py bottle.dat

Running Time: 0.06571698188781738


In [ ]:
%%writefile evolve_index_cyt.pyx

import numpy as np
cimport numpy as cnp
import cython

@cython.boundscheck(False)
@cython.wraparound(False)
@cython.cdivision(True)

def evolve_index_cyt(cnp.ndarray[cnp.double_t , ndim =2]u, cnp.ndarray[cnp.double_t , ndim =2]u_previous, double a, double dt, double dx2, double dy2):
    
    del_sqrd_u = (u_previous[:-2, 1:-1] - 2*u_previous[1:-1, 1:-1] + u_previous[2:, 1:-1]) / dx2 + (u_previous[1:-1, :-2] - 2*u_previous[1:-1, 1:-1] + u_previous[1:-1, 2:]) / dy2 
    
    u[1:-1,1:-1] = u_previous[1:-1,1:-1] + dt * a *  del_sqrd_u

    u_previous[:,:] = u[:,:]

In [ ]:
%%writefile heat_setup.py

from distutils.core import setup, Extension
from Cython.Build import cythonize
import numpy


setup(ext_modules = cythonize("evolve_index_cyt.pyx"),include_dirs=[numpy.get_include()])

In [ ]:
!python heat_setup.py build_ext --inplace

In [ ]:
!python heat_equation_index.py bottle.dat